In [15]:
import pandas as pd
import numpy as np

In [250]:
vt = pd.read_csv('vitals_trajectory.csv')

<ipython-input-250-64f1363dbd35>:1: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  vt = pd.read_csv('vitals_trajectory.csv')


## Filter  & standardization
MODS=1 on Day1, minute to hour and other cleaning

In [251]:
# drop completely redundant rows and keep MODS=day1 patients
all_sp = vt.drop('event_units',axis = 1).drop_duplicates()
mods_day1 = all_sp[all_sp['mods_day1']==1].drop('mods_day1',axis = 1)

In [252]:
# convert time from min to hour, reorder dataframe and clean age_group notation
mods_day1['event_hour'] = mods_day1['event_time'].div(60)
mods_day1['died_hour'] = mods_day1['died_time'].div(60*24)
mods_day1 = mods_day1.sort_values(by=['hospital_id','age_group','EncID','event_time','event_name'])
mods_day1['age_group'] = [i.split('.')[1] for i in mods_day1['age_group'].tolist()]
mods_day1

EncID hospital_id       age_group  mods_day7  died_in_hosp  \
377547   10236 L2_P01         P01            1 mo          0             0   
645780   10236 L2_P01         P01            1 mo          0             0   
771672   10236 L2_P01         P01            1 mo          0             0   
995554   10236 L2_P01         P01            1 mo          0             0   
377548   10236 L2_P01         P01            1 mo          0             0   
...               ...         ...             ...        ...           ...   
5163515       990_P13         P13   144 to 216 mo          0             0   
5057237       990_P13         P13   144 to 216 mo          0             0   
5299321       990_P13         P13   144 to 216 mo          0             0   
5524450       990_P13         P13   144 to 216 mo          0             0   
5741038       990_P13         P13   144 to 216 mo          0             0   

         died_time event_name  event_time  event_value  event_hour  died_hour  
377547         NaN      PULSE         4.0        169.0    0.066667        NaN  
645780         NaN   PULSE_OX         4.0         99.0    0.066667        NaN  
771672         NaN  RESP_RATE         4.0         47.0    0.066667        NaN  
995554         NaN       TEMP         4.0         36.5    0.066667        NaN  
377548         NaN      PULSE         9.0        168.0    0.150000        NaN  
...            ...        ...         ...          ...         ...        ...  
5163515        NaN        MAP      1434.0         68.0   23.900000        NaN  
5057237        NaN      PULSE      1434.0         96.0   23.900000        NaN  
5299321        NaN   PULSE_OX      1434.0        100.0   23.900000        NaN  
5524450        NaN  RESP_RATE      1434.0         26.0   23.900000        NaN  
5741038        NaN        SBP      1434.0         97.0   23.900000        NaN  

[3455399 rows x 11 columns]

## Population characteristics

In [237]:
# number of MODS=1 on day 1 versus all patients
print(mods_day1['EncID'].nunique(), all_sp['EncID'].nunique())

12845 38398


In [238]:
# mods day 7 difference between mods on day1 and all patients
print(mods_day1.groupby('EncID').first()['mods_day7'].value_counts(normalize=True), all_sp.groupby('EncID').first()['mods_day7'].value_counts(normalize=True), sep='\n')

0    0.710315
1    0.289685
Name: mods_day7, dtype: float64
0    0.883119
1    0.116881
Name: mods_day7, dtype: float64


In [239]:
# death in hospital difference
print(mods_day1.groupby('EncID').first()['died_in_hosp'].value_counts(normalize=True), all_sp.groupby('EncID').first()['died_in_hosp'].value_counts(normalize=True), sep='\n')

0    0.892254
1    0.107746
Name: died_in_hosp, dtype: float64
0    0.953018
1    0.046982
Name: died_in_hosp, dtype: float64


In [240]:
# death in hospital count difference
print(mods_day1.groupby('EncID').first()['died_in_hosp'].value_counts(), all_sp.groupby('EncID').first()['died_in_hosp'].value_counts(), sep='\n')

0    11461
1     1384
Name: died_in_hosp, dtype: int64
0    36594
1     1804
Name: died_in_hosp, dtype: int64


In [241]:
# proportion in each group for mods day1
mods_day1.groupby('EncID').first()['age_group'].value_counts(normalize=True)

 60 to 143 mo     0.254885
 144 to 216 mo    0.242507
 2 to 11 mo       0.175710
 24 to 59 mo      0.170027
 12 to 24 mo      0.116388
 1 mo             0.040483
Name: age_group, dtype: float64

## Clean death time
replace negative values with last vital time

In [255]:
# replace negative death times with time of last vital
tmp = mods_day1.groupby('EncID').last()
last_event_time = tmp[tmp['died_time']<0][['event_time','event_hour']]
neg_death_id = last_event_time.index.tolist()
neg_death_time = last_event_time['event_time'].tolist()
neg_death_hr = last_event_time['event_hour'].tolist()
for idx,val in enumerate(neg_death):
    #print(mods_day1.loc[mods_day1.index ==val, 'died_time'])
    mods_day1.loc[mods_day1['EncID'] ==val, 'died_time'] = neg_death_time[idx]
    mods_day1.loc[mods_day1['EncID'] ==val, 'died_hour'] = neg_death_hr[idx]

In [243]:
mods_day1.groupby('EncID').first()['died_hour'].describe()

count    1520.000000
mean       65.801754
std       197.342752
min         0.000000
25%         2.000000
50%         6.635417
75%        31.105556
max      1888.763889
Name: died_hour, dtype: float64

In [256]:
mods_day1 = mods_day1.drop(['event_time','died_time'],axis = 1)

## Select first 12hr of vitals

In [257]:
#mods_day1.to_csv('mods_day1.csv',index=False)
mods_day1_12hr = mods_day1[mods_day1['event_hour']<13]
#mods_day1_12hr.to_csv('mods_day1_12hr.csv',index=False)

In [258]:
# available vitals in first 12 hours
mods_day1_12hr['event_name'].value_counts()

PULSE        346133
PULSE_OX     341325
MAP          340268
SBP          328342
RESP_RATE    314790
FIO2         168956
TEMP         134148
SF_RATIO     103497
Name: event_name, dtype: int64

## Re-calculate SF Ratio
Hourly SF ratio = hourly average of pulse_ox / hourly average of fio2

In [294]:
# re-derive sf_ratio
sf_ratio = mods_day1_12hr[mods_day1_12hr['event_name'].isin(['PULSE_OX','FIO2','SF_RATIO'])][['EncID','event_name','event_hour','event_value']]
sf_ratio['event_hr_floor'] = np.floor(sf_ratio['event_hour'])
pulse_ox = sf_ratio[sf_ratio['event_name'] == 'PULSE_OX']
fio2 = sf_ratio[sf_ratio['event_name'] == 'FIO2']
pulse_ox_ave = pd.DataFrame(pulse_ox.groupby(['EncID','event_hr_floor'])['event_value'].mean())
fio2_ave = pd.DataFrame(fio2.groupby(['EncID','event_hr_floor'])['event_value'].mean())

In [326]:
# rederive sf_ratio
calc_sfratio = []
for i in pulse_ox_ave.index:
    encid = i[0]
    hr_floor = i[1]
    if (fio2_ave.index == i).any():
        fio2_row = fio2_ave.iloc[(fio2_ave.index.get_level_values('EncID') == encid) & (fio2_ave.index.get_level_values('event_hr_floor') == hr_floor)]
        fio2 = fio2_row['event_value'].tolist()[0]
        pulseox = pulse_ox_ave.loc[[i]]['event_value'].tolist()[0]
        calc = [encid, hr_floor, pulseox/fio2]
        calc_sfratio.append(calc)
        print(calc)

['1000044335_P05', 0.0, 191.0]
['1000044335_P05', 2.0, 184.0]
['1000044335_P05', 3.0, 194.0]
['1000044335_P05', 5.0, 200.0]
['1000044335_P05', 6.0, 200.0]
['1000044335_P05', 7.0, 200.0]
['1000044335_P05', 8.0, 188.0]
['1000044335_P05', 9.0, 200.0]
['1000044335_P05', 10.0, 200.0]
['1000044335_P05', 11.0, 250.0]
['1000044335_P05', 12.0, 250.0]
['100005_P12', 0.0, 67.875]
['100005_P12', 1.0, 91.25778331257783]
['100005_P12', 2.0, 96.21621621621621]
['100005_P12', 3.0, 106.11764705882354]
['100005_P12', 4.0, 135.57692307692307]
['100005_P12', 6.0, 149.94285714285712]
['100005_P12', 9.0, 94.44444444444444]
['100005_P12', 10.0, 130.0]
['100005_P12', 12.0, 135.0]
['1000099114_P06', 0.0, 165.0]
['1000099114_P06', 1.0, 161.25]
['1000099114_P06', 3.0, 100.0]
['1000099114_P06', 5.0, 136.36363636363635]
['1000099114_P06', 7.0, 125.0]
['1000099114_P06', 9.0, 98.0]
['1000099114_P06', 11.0, 165.83333333333334]
['100011_P12', 0.0, 250.0]
['100011_P12', 1.0, 245.0]
['100011_P12', 2.0, 250.0]
['100011_P

['10004003_P04', 6.0, 218.5185185185185]
['10004003_P04', 7.0, 277.14285714285717]
['10004003_P04', 8.0, 280.0]
['10004003_P04', 9.0, 207.3684210526316]
['10004003_P04', 10.0, 282.8571428571429]
['10004003_P04', 11.0, 280.952380952381]
['10004003_P04', 12.0, 280.0]
['10004005_P04', 0.0, 230.76923076923077]
['10004005_P04', 1.0, 330.0]
['10004005_P04', 2.0, 333.33333333333337]
['10004005_P04', 3.0, 333.33333333333337]
['10004005_P04', 4.0, 330.0]
['10004005_P04', 5.0, 333.33333333333337]
['10004005_P04', 6.0, 325.0]
['10004005_P04', 7.0, 316.6666666666667]
['10004005_P04', 8.0, 333.33333333333337]
['10004005_P04', 9.0, 333.33333333333337]
['10004005_P04', 10.0, 333.33333333333337]
['10004005_P04', 11.0, 318.33333333333337]
['10004005_P04', 12.0, 326.6666666666667]
['10004006_P04', 8.0, 290.76923076923083]
['10004006_P04', 9.0, 265.7142857142857]
['10004006_P04', 10.0, 268.5714285714286]
['10004006_P04', 11.0, 282.8571428571429]
['10004006_P04', 12.0, 280.0]
['10004008_P04', 0.0, 95.3333

['10004064_P04', 11.0, 333.33333333333337]
['10004064_P04', 12.0, 333.33333333333337]
['10004065_P04', 0.0, 130.95890410958904]
['10004065_P04', 1.0, 158.33333333333334]
['10004065_P04', 2.0, 197.0]
['10004065_P04', 3.0, 196.0]
['10004065_P04', 4.0, 198.0]
['10004065_P04', 5.0, 222.22222222222223]
['10004065_P04', 6.0, 200.0]
['10004065_P04', 7.0, 250.0]
['10004065_P04', 8.0, 250.0]
['10004065_P04', 9.0, 237.5]
['10004065_P04', 10.0, 240.0]
['10004065_P04', 11.0, 240.0]
['10004065_P04', 12.0, 237.5]
['10004072_P04', 0.0, 118.12499999999999]
['10004072_P04', 1.0, 162.91666666666669]
['10004072_P04', 2.0, 176.36363636363637]
['10004072_P04', 3.0, 242.5]
['10004072_P04', 4.0, 245.0]
['10004072_P04', 5.0, 242.5]
['10004072_P04', 6.0, 243.75]
['10004072_P04', 7.0, 160.0]
['10004072_P04', 8.0, 235.0]
['10004072_P04', 9.0, 237.5]
['10004072_P04', 10.0, 262.7272727272727]
['10004072_P04', 11.0, 245.0]
['10004072_P04', 12.0, 282.8571428571429]
['10004075_P04', 0.0, 250.0]
['10004075_P04', 1.0, 

['10004110_P04', 4.0, 232.5]
['10004110_P04', 5.0, 240.0]
['10004110_P04', 6.0, 232.5]
['10004110_P04', 7.0, 237.5]
['10004110_P04', 8.0, 243.75]
['10004110_P04', 9.0, 240.0]
['10004110_P04', 10.0, 238.75]
['10004110_P04', 11.0, 241.25]
['10004110_P04', 12.0, 184.76190476190476]
['10004112_P04', 0.0, 131.31034482758622]
['10004112_P04', 1.0, 138.57142857142858]
['10004112_P04', 2.0, 325.0]
['10004112_P04', 3.0, 326.6666666666667]
['10004112_P04', 4.0, 320.0]
['10004112_P04', 6.0, 275.7142857142857]
['10004112_P04', 7.0, 323.33333333333337]
['10004112_P04', 10.0, 244.16666666666666]
['10004112_P04', 11.0, 259.99999999999994]
['10004112_P04', 12.0, 189.2]
['10004113_P04', 0.0, 247.5]
['10004113_P04', 4.0, 285.7142857142857]
['10004113_P04', 7.0, 274.2857142857143]
['10004113_P04', 11.0, 277.14285714285717]
['10004114_P04', 3.0, 213.33333333333331]
['10004114_P04', 4.0, 208.88888888888889]
['10004114_P04', 6.0, 222.22222222222223]
['10004114_P04', 8.0, 285.7142857142857]
['10004114_P04', 

['10004169_P04', 11.0, 178.0]
['10004169_P04', 12.0, 232.15686274509804]
['10004176_P04', 0.0, 123.69565217391305]
['10004176_P04', 1.0, 196.0]
['10004176_P04', 2.0, 198.0]
['10004176_P04', 3.0, 242.5]
['10004176_P04', 4.0, 326.6666666666667]
['10004176_P04', 5.0, 323.33333333333337]
['10004176_P04', 6.0, 320.0]
['10004176_P04', 7.0, 316.6666666666667]
['10004176_P04', 8.0, 313.33333333333337]
['10004176_P04', 9.0, 316.6666666666667]
['10004176_P04', 10.0, 250.66666666666666]
['10004176_P04', 11.0, 265.7142857142857]
['10004176_P04', 12.0, 268.5714285714286]
['10004183_P04', 0.0, 196.0]
['10004183_P04', 1.0, 240.0]
['10004183_P04', 2.0, 242.5]
['10004183_P04', 3.0, 247.5]
['10004183_P04', 4.0, 232.5]
['10004183_P04', 5.0, 240.0]
['10004183_P04', 6.0, 237.5]
['10004183_P04', 7.0, 230.0]
['10004183_P04', 8.0, 242.5]
['10004183_P04', 9.0, 235.0]
['10004183_P04', 10.0, 240.0]
['10004183_P04', 11.0, 235.0]
['10004183_P04', 12.0, 230.0]
['10004186_P04', 0.0, 123.8709677419355]
['10004186_P04

...

['95723270_P05', 9.0, 237.5]
['95723270_P05', 12.0, 241.25]
['957_P10', 0.0, 224.8]
['957_P10', 1.0, 297.6]
['957_P10', 2.0, 306.6666666666667]
['957_P10', 4.0, 428.5714285714286]
['957_P10', 5.0, 440.4761904761905]
['957_P10', 6.0, 447.61904761904765]
['957_P10', 7.0, 438.09523809523813]
['957_P10', 8.0, 454.76190476190476]
['957_P10', 9.0, 465.95238095238096]
['957_P10', 10.0, 471.42857142857144]
['957_P10', 11.0, 475.0]
['957_P10', 12.0, 473.80952380952385]
['958538736_P05', 0.0, 188.0]
['958538736_P05', 2.0, 245.0]
['958538736_P05', 4.0, 280.0]
['958538736_P05', 8.0, 316.6666666666667]
['958538736_P05', 10.0, 323.33333333333337]
['9589 L2_P01', 6.0, 476.1904761904762]
['9589 L2_P01', 11.0, 476.1904761904762]
['958_P10', 0.0, 474.6031746031746]
['958_P10', 1.0, 465.87301587301585]
['958_P10', 2.0, 460.0]
['958_P10', 3.0, 468.25396825396825]
['958_P10', 4.0, 457.14285714285717]
['958_P10', 5.0, 476.1904761904762]
['958_P10', 6.0, 476.1904761904762]
['958_P10', 7.0, 476.1904761904762]

['964297847_P05', 12.0, 400.0]
['964_P13', 0.0, 194.0]
['964_P13', 1.0, 194.0]
['964_P13', 2.0, 156.66666666666669]
['964_P13', 3.0, 190.0]
['964_P13', 4.0, 198.0]
['964_P13', 5.0, 198.0]
['964_P13', 6.0, 200.0]
['964_P13', 7.0, 215.55555555555554]
['964_P13', 8.0, 242.5]
['964_P13', 9.0, 242.5]
['964_P13', 10.0, 277.14285714285717]
['964_P13', 11.0, 280.0]
['964_P13', 12.0, 277.14285714285717]
['9653_P03', 0.0, 99.0]
['9653_P03', 1.0, 97.0]
['9653_P03', 2.0, 93.0]
['9653_P03', 3.0, 89.5]
['9653_P03', 4.0, 94.0]
['9653_P03', 5.0, 83.0]
['9653_P03', 6.0, 96.0]
['9653_P03', 7.0, 98.0]
['9653_P03', 9.0, 100.0]
['9653_P03', 11.0, 104.44444444444444]
['9662 L2_P01', 8.0, 100.0]
['9668 L2_P01', 0.0, 96.0]
['9668 L2_P01', 2.0, 250.0]
['9668 L2_P01', 5.0, 243.75]
['966916432_P06', 0.0, 166.11111111111111]
['966916432_P06', 1.0, 245.0]
['9687 L2_P01', 0.0, 196.51056014692378]
['9687 L2_P01', 4.0, 256.4102564102564]
['9687 L2_P01', 7.0, 156.9747899159664]
['9687 L2_P01', 10.0, 137.85714285714286

['9774 L2_P01', 4.0, 200.0]
['9774 L2_P01', 7.0, 184.0]
['9774 L2_P01', 11.0, 132.85714285714286]
['977533558_P06', 0.0, 113.92857142857142]
['977533558_P06', 2.0, 99.07142857142857]
['977533558_P06', 4.0, 100.0]
['977533558_P06', 6.0, 99.8]
['977533558_P06', 7.0, 124.58333333333333]
['977533558_P06', 10.0, 198.0]
['977533558_P06', 12.0, 199.0]
['9776 L2_P01', 0.0, 96.5]
['9776 L2_P01', 8.0, 99.0]
['9778 L2_P01', 1.0, 285.7142857142857]
['9778 L2_P01', 6.0, 333.33333333333337]
['9778 L2_P01', 10.0, 333.33333333333337]
['977818609_P06', 1.0, 113.33333333333333]
['977818609_P06', 2.0, 154.16666666666669]
['977818609_P06', 3.0, 176.36363636363635]
['977818609_P06', 5.0, 179.09090909090907]
['977818609_P06', 7.0, 193.33333333333334]
['977818609_P06', 8.0, 178.18181818181816]
['977818609_P06', 11.0, 180.9090909090909]
['977818609_P06', 12.0, 245.0]
['977_P10', 0.0, 178.57142857142856]
['977_P10', 1.0, 245.21739130434784]
['977_P10', 2.0, 265.7142857142857]
['977_P10', 3.0, 265.7142857142858

['985394983_P06', 2.0, 247.5]
['985394983_P06', 4.0, 247.5]
['985394983_P06', 7.0, 247.5]
['985394983_P06', 8.0, 245.0]
['985394983_P06', 11.0, 240.0]
['985394983_P06', 12.0, 244.16666666666666]
['9858 L2_P01', 1.0, 166.66666666666669]
['9858 L2_P01', 2.0, 166.66666666666669]
['986483044_P06', 0.0, 330.0]
['986483044_P06', 2.0, 471.42857142857144]
['986483044_P06', 4.0, 452.3809523809524]
['986483044_P06', 6.0, 452.3809523809524]
['986483044_P06', 10.0, 378.6666666666667]
['986_P10', 0.0, 253.0434782608696]
['986_P10', 1.0, 277.14285714285717]
['986_P10', 3.0, 285.7142857142857]
['986_P10', 4.0, 285.7142857142857]
['986_P10', 5.0, 280.0]
['986_P10', 6.0, 330.0]
['986_P10', 7.0, 320.0]
['986_P10', 8.0, 344.8275862068965]
['986_P10', 9.0, 333.33333333333337]
['986_P10', 10.0, 330.0]
['986_P10', 11.0, 323.33333333333337]
['986_P10', 12.0, 290.0]
['986_P13', 0.0, 137.14285714285714]
['986_P13', 1.0, 138.57142857142858]
['986_P13', 2.0, 140.0]
['986_P13', 3.0, 139.2857142857143]
['986_P13',

['9975_P02', 11.0, 162.5]
['9975_P02', 12.0, 166.66666666666669]
['997_P13', 1.0, 87.6]
['997_P13', 2.0, 86.75]
['997_P13', 4.0, 93.8]
['998_P10', 0.0, 105.67567567567568]
['998_P10', 1.0, 140.71428571428572]
['998_P10', 2.0, 140.0]
['998_P10', 3.0, 142.85714285714286]
['998_P10', 4.0, 137.14285714285714]
['998_P10', 5.0, 198.0]
['998_P10', 7.0, 280.0]
['998_P10', 8.0, 306.3157894736842]
['998_P10', 9.0, 313.33333333333337]
['998_P10', 10.0, 301.53846153846155]
['998_P10', 11.0, 310.0]
['998_P10', 12.0, 310.0]
['998_P13', 0.0, 124.44444444444444]
['998_P13', 1.0, 93.83333333333333]
['998_P13', 2.0, 106.5079365079365]
['998_P13', 3.0, 108.05555555555556]
['998_P13', 5.0, 149.23076923076923]
['998_P13', 6.0, 147.69230769230768]
['998_P13', 7.0, 173.91304347826087]
['998_P13', 8.0, 194.0]
['998_P13', 9.0, 194.0]
['998_P13', 10.0, 192.0]
['998_P13', 11.0, 118.66666666666667]
['998_P13', 12.0, 112.54901960784314]
['99917969_P05', 0.0, 164.8148148148148]
['99917969_P05', 1.0, 238.125]
['9991

In [376]:
# compare size of old sf_ratio and newly derived
# old sf ratio
sf_ratio_only = sf_ratio[sf_ratio['event_name'] == 'SF_RATIO']
sf_ratio_old_ave = pd.DataFrame(sf_ratio_only.groupby(['EncID','event_hr_floor'])['event_value'].mean())
print(sf_ratio_old_ave.shape[0], len(calc_sfratio))

59369 96044


In [374]:
# format newly derived sf_ratio to df
new_sfratio_df = pd.DataFrame(calc_sfratio)
new_sfratio_df.columns = ['EncID','event_hour','event_value']
new_sfratio_df['event_name'] = 'SF_RATIO'

In [375]:
new_sfratio_df

EncID  event_hour  event_value event_name
0      1000044335_P05         0.0        191.0   SF_RATIO
1      1000044335_P05         2.0        184.0   SF_RATIO
2      1000044335_P05         3.0        194.0   SF_RATIO
3      1000044335_P05         5.0        200.0   SF_RATIO
4      1000044335_P05         6.0        200.0   SF_RATIO
...               ...         ...          ...        ...
96039         999_P10         8.0        400.0   SF_RATIO
96040         999_P10         9.0        396.0   SF_RATIO
96041         999_P10        10.0        396.0   SF_RATIO
96042         999_P10        11.0        400.0   SF_RATIO
96043         999_P10        12.0        400.0   SF_RATIO

[96044 rows x 4 columns]

## Clean metadata of patients
remove duplicate death time

In [378]:
# extract metadata for each patient
meta = mods_day1_12hr[['EncID','hospital_id','age_group','mods_day7','died_in_hosp','died_hour']].drop_duplicates()

In [379]:
# check id of patients with multiple meta data
tmp = pd.DataFrame(meta['EncID'].value_counts())
dup_meta = tmp[tmp['EncID']>1].index.tolist()
meta_dup = meta[meta['EncID'].isin(dup_meta)]
# round to nearest thousandth and remove duplicate due to small time difference
meta_dup['died_hour_round'] = round(meta_dup['died_hour'],2)
meta_dup = meta_dup.drop('died_hour',axis = 1)
meta_dup = meta_dup.drop_duplicates()
# no more dup
meta_dup['EncID'].value_counts()

<ipython-input-379-ccc85edddd1c>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  meta_dup['died_hour_round'] = round(meta_dup['died_hour'],2)


17111_P02    1
12687_P02    1
19992_P02    1
24390_P02    1
24510_P02    1
            ..
37113_P02    1
40197_P02    1
5309_P02     1
8600_P02     1
8583_P02     1
Name: EncID, Length: 65, dtype: int64

In [380]:
meta['died_hour_round'] = round(meta['died_hour'], 2)
meta = meta.drop('died_hour', axis = 1)
meta = meta.drop_duplicates()

In [381]:
meta

EncID hospital_id       age_group  mods_day7  died_in_hosp  \
377547   10236 L2_P01         P01            1 mo          0             0   
547648   12801 L2_P01         P01            1 mo          0             0   
552534   13654 L2_P01         P01            1 mo          0             0   
552975   13681 L2_P01         P01            1 mo          1             1   
465088   14435 L2_P01         P01            1 mo          1             1   
...               ...         ...             ...        ...           ...   
5387151       964_P13         P13   144 to 216 mo          0             0   
5162978        96_P13         P13   144 to 216 mo          0             0   
5399799        97_P13         P13   144 to 216 mo          0             0   
5387387       984_P13         P13   144 to 216 mo          0             0   
5387466       990_P13         P13   144 to 216 mo          0             0   

         died_hour_round  
377547               NaN  
547648               NaN  
552534               NaN  
552975               4.0  
465088               1.0  
...                  ...  
5387151              NaN  
5162978              NaN  
5399799              NaN  
5387387              NaN  
5387466              NaN  

[12842 rows x 6 columns]

## Calculate hourly average for all vitals
replace vitals that have multiple measurements in an hour with hourly average

In [421]:
# extract vitals only dataframe
vitals = mods_day1_12hr[['EncID','event_name','event_hour','event_value']]
vitals['event_hr_floor'] = np.floor(vitals['event_hour'])  
             
# helper for calculating hourly average
def hr_ave(vit):
    df = vitals[vitals['event_name'] == vit]
    df = pd.DataFrame(df.groupby(['EncID','event_hr_floor'])['event_value'].mean())
    df['EncID'] = [i[0] for i in df.index.tolist()]
    df['event_hour'] = [i[1] for i in df.index.tolist()]
    df = df.reset_index(drop=True)
    df = df[['EncID', 'event_hour','event_value']]
    df['event_name'] = vit
    return df

<ipython-input-421-0bc9261d334b>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  vitals['event_hr_floor'] = np.floor(vitals['event_hour'])


In [422]:
# calculate hourly mean for all vitals PULSE, MAP, SBP, RESP_RATE, TEMP
pulse_ave = hr_ave('PULSE')
map_ave = hr_ave('MAP')
sbp_ave = hr_ave('SBP')
resp_ave = hr_ave('RESP_RATE')
temp_ave = hr_ave('TEMP')

In [423]:
print(pulse_ave.shape, map_ave.shape, sbp_ave.shape, resp_ave.shape, temp_ave.shape)

(154256, 4) (141212, 4) (141921, 4) (150122, 4) (94331, 4)


## Merge new vitals with metadata

In [429]:
# concatenation of vitals
tmp = pd.concat([pulse_ave, map_ave], axis=0)
tmp = pd.concat([tmp, sbp_ave], axis=0)
tmp = pd.concat([tmp, resp_ave], axis=0)
tmp = pd.concat([tmp, temp_ave], axis=0)
vital_hrave = pd.concat([tmp, new_sfratio_df], axis=0)

In [435]:
# merge with meta data
new_df = vital_hrave.merge(meta, on='EncID', how='left')
new_df.sort_values(by=['hospital_id','age_group','EncID','event_hour','event_name'])

EncID  event_hour  event_value event_name hospital_id  \
188669  10236 L2_P01         0.0    55.666667        MAP         P01   
35851   10236 L2_P01         0.0   169.800000      PULSE         P01   
472933  10236 L2_P01         0.0    41.400000  RESP_RATE         P01   
329905  10236 L2_P01         0.0    78.000000        SBP         P01   
708482  10236 L2_P01         0.0   323.333333   SF_RATIO         P01   
...              ...         ...          ...        ...         ...   
295039       986_P13        12.0    98.000000        MAP         P13   
153792       986_P13        12.0    94.000000      PULSE         P13   
587055       986_P13        12.0    21.000000  RESP_RATE         P13   
436959       986_P13        12.0   132.000000        SBP         P13   
777630       986_P13        12.0   194.000000   SF_RATIO         P13   

            age_group  mods_day7  died_in_hosp  died_hour_round  
188669           1 mo          0             0              NaN  
35851            1 mo          0             0              NaN  
472933           1 mo          0             0              NaN  
329905           1 mo          0             0              NaN  
708482           1 mo          0             0              NaN  
...               ...        ...           ...              ...  
295039   60 to 143 mo          0             0              NaN  
153792   60 to 143 mo          0             0              NaN  
587055   60 to 143 mo          0             0              NaN  
436959   60 to 143 mo          0             0              NaN  
777630   60 to 143 mo          0             0              NaN  

[777886 rows x 9 columns]

In [436]:
new_df.to_csv('vitals_trajectory_cleaned.csv',index=False)